# Analyzing The Wanderers

This notebook analyzes the ["The Wanderers"](https://wanderers.ai/) NFT collection with a focus on their traits and the prices they can realize. [Visit the repository](https://github.com/ymyke) for more notebooks on other projects, to use the code, or to contribute.

Important: This notebook uses [Plotly](https://plotly.com/python/) mostly to visualize data. Plotly charts won't be rendered in Githubs notebook viewer. So please [view this notebook on nbviewer](https://nbviewer.org/github/ymyke/niftylytics/blob/main/the_wanderers.ipynb) (or on your local installation after cloning the repo). Note that nbviewer caches notebooks and sometimes takes a long time to pick up a new version.

On the upside, all the Plotly charts are interactive. You can zoom, hover, pan, etc. Zooming is especially important due to the outliers in some the data so you can zoom in on the interesting parts.

Note also that the Plotly charts take a long time to load in the browser because there are a lot of charts with many data points.

In [1]:
import plotly.io as pio
pio.renderers.default = "notebook_connected"

## Get the assets

Note that this takes a long time, i.e. up to 10 minutes. Also note the timestamp below,
that is when the information was last retrieved.

In [2]:
import datetime
from opensea import retrieve_assets

ids = list(range(0, 8888))
assets = retrieve_assets(token_ids=ids, contract="0x8184a482A5038B124d933B779E0Ea6e0fb72F54E")
print(datetime.datetime.now())


............................................................................................................................................................................................................................................................................................................................................................................................................................................................. -- All 8888 assets retrieved.
2021-11-01 15:37:23.184366


## Build a dataframe

Check the trait types there are. We'll see that 1) different assets can have different numbers of traits, 2) the same asset can have traits with the same name, i.e. "Celestial Body".

In [3]:
[", ".join(t["trait_type"] for t in a["traits"]) for a in assets][:10]

['Planet, Anomaly, Music, Cockpit, Left Arm, Window, Celestial Body, Celestial Body, Panel 3, Ships, Right Arm, Panel 4, Panel 2',
 'Planet, Cockpit, Left Arm, Right Arm, Window, Celestial Body, Music, Panel 1, Celestial Body',
 'Window, Left Arm, Music, Panel 2, Cockpit, Right Arm, Panel 4, Planet, Celestial Body',
 'Panel 2, Left Arm, Panel 1, Panel 3, Panel 4, Cockpit, Music, Window, Right Arm, Celestial Body',
 'Anomaly, Panel 5, Ships, Cockpit, Right Arm, Celestial Body, Window, Music, Left Arm',
 'Panel 4, Celestial Body, Window, Celestial Body, Right Arm, Cockpit, Music, Panel 5, Left Arm',
 'Panel 1, Panel 4, Cockpit, Right Arm, Ships, Window, Music, Left Arm, Panel 3',
 'Cockpit, Panel 3, Panel 4, Right Arm, Panel 5, Music, Window, Left Arm',
 'Cockpit, Right Arm, Left Arm, Panel 1, Ships, Panel 5, Window, Music',
 'Panel 4, Ships, Right Arm, Planet, Panel 3, Cockpit, Left Arm, Window, Celestial Body, Music, Celestial Body']

All the possible celestial bodies there are:

In [4]:
set([t["value"]  for a in assets for t in a["traits"] if t["trait_type"] == "Celestial Body"])

{'Blue Galaxy',
 'Blue Stars',
 'Green Stars',
 'Large Green Galaxy',
 'Large Purple Galaxy',
 'Purple Galaxy',
 'Purple Stars',
 'Red Stars'}

We will count the number of Celestial Bodies as well as the number of stars and galaxies when tabulating all the information into a dataframe:

(Large vs not large galaxies will be ignored; could be added as some point in the future.)

In [5]:
import numpy as np
import pandas as pd
import helpers
df, traits = helpers.turn_assets_into_df_wanderers_variant(assets)
hoverdata = [ "Name", *traits, "Probscore"]

In [6]:
assert set(df.LPsymbol.unique()) == set(["ETH", "WETH", np.nan]), """
This sheet does not do currency conversion at the moment and therefore 
assumes all prices are in (W)ETH. But there are more symbols in the input 
data which would lead to apples being compared to ranges below. Aborting.
"""

## How many pieces have a last price on OpenSea?

In [7]:
print(f"{df[~df.Lastprice.isna()].shape[0] / df.shape[0]:.0%}")

79%


## How are prices evolving over time?

Note that this only takes into account the last sale of each piece.

In [8]:
import plotly.express as px
import plotly.graph_objects as go
import matplotlib.pyplot as plt

plt.rcParams["figure.figsize"] = (20, 8)
pd.plotting.register_matplotlib_converters()

fig = px.scatter(df, x="LPdate", y="Lastprice", hover_data=hoverdata)
fig.show()

## Price levels today

In [9]:
fig = px.histogram(df, x="Lastprice", marginal="box", hover_data=hoverdata)
fig.show()

## How frequent are the different traits?

In [10]:
pd.set_option("display.max_columns", None)

from IPython.display import display
for trait in sorted(traits.keys()):
    display(
        pd.DataFrame(df[trait].value_counts(normalize=False, sort=True, ascending=True)).transpose()
    )


Monolith  Purple Wormhole  Glitch Wormhole  White Wormhole  \
Anomaly        63              231              238             239   

         Blue Wormhole  Pink Wormhole     -  
Anomaly            254            256  7607

6  5   4    3     2     0     1
Celestial Bodies  2  9  99  522  1886  2924  3446

Cat    -  Glyphs  Hexagon  Sound  Dots  Chart  Falcon  Retro  \
Cockpit   82  134     173      665    678   697    703     704    707   

         Circles  Target  Dotface  Pink  Radar  Planet  
Cockpit      718     718      724   724    728     733

3    2     1     0
Galaxies  31  308  2393  6156

Joint  ETH  Skull  Porn  Jar Eyes  Jar Shrooms  Alien Joint  \
Left Arm     24   33     34    36        36           39           42   

          Robo Charge  Hotdog  Goldfish  Bong  Whiskey  8-Ball  Takeout  \
Left Arm           44      44        66    81       83      84       86   

          Banana  Pizza  Chicken  Watch  Syringe  Orbit  Jar  Hook  Booze  \
Left Arm      87     89       89     89       89     90   90    90     92   

          Coffee  Knife  Bone  Egg  Flag  Burn  Boba  Laser  Flower  Wine  \
Left Arm      92     93    94   98    98    99   100    106     106   106   

          Shrooms  Zombie    -  Treasure  Slider  V Steering  Shifter  Tablet  \
Left Arm      106     112  134       339     346         365      367     370   

          Hologram  Handcrank  Antennae  Thrust  Big Button  Swipe  \
Left Arm       372        376       376     379         380    384   

          Button Row Slider  Alien Gearshift  Buttons  Button Row  Gearshift  
Left Arm                386              390      390         393        394

...

Joint  ETH  Jar Shrooms  Skull  Hotdog  Robo Charge  Alien Joint  \
Right Arm     30   31           32     36      39           40           40   

           Porn  Jar Eyes  Jar  Knife  Bong  Flag  Orbit  8-Ball  Pizza  \
Right Arm    40        40   78     78    82    82     84      84     87   

           Zombie  Banana  Bone  Boba  Egg  Syringe  Whiskey  Takeout  Hook  \
Right Arm      88      88    89    95   95       97       98      100   100   

           Wine  Coffee  Laser  Booze  Shrooms  Watch  Goldfish  Burn  \
Right Arm   100     100    102    104      104    104       106   107   

           Chicken  Flower    -  Alien Gearshift  Handcrank  Hologram  Slider  \
Right Arm      108     108  134              315        329       332     346   

           Swipe  Buttons  Tablet  Button Row Slider  V Steering  Gearshift  \
Right Arm    361      374     375                377         382        383   

           Antennae  Shifter  Thrust  Big Button  Treasure  Button Row  
Right Arm       389      390     392         396       403         414

Space Station  Guardian (active)  Large Battle  Cargo  Flyby Trio  \
Ships            144                155           157    171         174   

       Guardian (rogue)  Battle (alt)  Flyby Dogfight  Triforce  UFO  \
Ships               175           178             186       186  188   

       Destroyed Freighter  Flyby  Battle  Fleet  Docking  Freighter  \
Ships                  188    189     189    193      194        195   

       Freighter Battle     -  
Ships               209  5817

4    3     2     1     0
Stars  6  156  1095  3453  4178

-  Tubes  Eyes  ETH  Plants  Blue  Screens  Green  White  Bolt  \
Window  134    184   196  215     428   724      735    756    767   774   

        Crack  Wires  Purple  Pink  Dice  
Window    780    781     784   804   826

Guardian Marked, RADIOACTIVE  Warp Squad Sixteen  Guardian Marked  \
special                             1                  16               40   

         RADIOACTIVE     -  
special           82  8749

## How much do people pay for the different traits?

**Some Observations**:

- The monolith anomaly commands much higher prices than other anomalies. It is also the most seldom anomaly.
- The more celestial bodies, the higher the price. Same with galaxies and stars. (4 stars is really seldom and outperforms 0-3 stars massively.)
- A cat cockpit slightly outperforms other cockpits. Interestingly, glyphs perform average, even though they are much rarer than average. No cockpit at all has a bad impact on price.
- Arms: Joints perform best, followed by ETH, bong, porn, alien joint, and skull. Flag is clearly worst (I wonder why?). Bongs perform much better than their rarity would suggest, whereas flags left perform much worse than their rarity would suggest (not so much for flags right, strangely).
- Music doesn't make a difference. Except no music at all, which is detrimental to price.
- Panels: Crypto, bounty, tetris, spam are the best preformers which is very much in line with their rarity.
- Planet: Anger orb and destroyed planet are clearly performing best and also rarest.
- Ships: Doesn't make much of a difference.
- Window: Doesn't make much of a difference.
- Special: Specials in general add to the value. Warp squad sixteen performs very high.
- Keep in mind that this doesn't take into account possible cross-correlations between the different traits. 


In [11]:
for trait in sorted(traits.keys()):

    fig = go.Figure()

    for traitvariant in (
        df.groupby(trait).median().sort_values("Lastprice", ascending=False).index
        ):
        fig.add_trace(
            go.Box(
                y=df[df[trait] == traitvariant].fillna("-").Lastprice.values,
                name=traitvariant,
                # boxpoints="all",
                jitter=0.2,
                whiskerwidth=0.2,
                marker_size=2,
                line_width=1,
            )
        )
    fig.update_layout(title=trait)
    fig.show()

## What is pricier, galaxies or stars?

There seems to be no fundamental difference between stars and galaxies. In either case, rarity is the differentiator: 3 galaxies is slightly rare, 4 stars is rare, 5 bodies overall is rare and 6 bodies is superrare – so these all command higher prices.

In [12]:
df["Celestialstype"] = df.apply(
    lambda x: "Starsonly"
    if x["Galaxies"] == 0
    else "Galaxiesonly"
    if x["Stars"] == 0
    else "Both",
    axis=1,
)
px.box(df, x="Celestial Bodies", y="Lastprice", color="Celestialstype", points="all", hover_data=hoverdata)

## Check if there's a bargain for any of the more lucrative traits

In [15]:
display(df[df["Anomaly"] != "-"].sort_values("Price").head(3))
display(df[df["Celestial Bodies"] >= 4].sort_values("Price").head(3))
display(df[df["Left Arm"].isin(["Joint", "Alien Joint", "Bong", "Skull", "Porn", "ETH"])].sort_values("Price").head(3))
# ...

Name  Price Psymbol  Lastprice LPsymbol              LPdate  Probscore  \
ID                                                                             
6598  6598  0.399     ETH      0.500      ETH 2021-09-27 00:05:08   0.021620   
5470  5470  0.450     ETH        NaN      NaN                 NaT   0.560865   
8885  8885  0.479     ETH      0.301      ETH 2021-09-01 16:03:51   0.217198   

             Anomaly  Celestial Bodies Cockpit  Galaxies    Left Arm  \
ID                                                                     
6598  White Wormhole                 0   Radar         0       Laser   
5470   Pink Wormhole                 1    Pink         1  V Steering   
8885   Pink Wormhole                 1    Dots         0      Slider   

               Music Panel 1 Panel 2   Panel 3          Panel 4 Panel 5  \
ID                                                                        
6598  Lone Planeteer       -       -  Low-poly                -     DNA   
5470    The Ponderer   Noisy       -         -                -       -   
8885    The Wanderer       -       -         -  Poplights (alt)       -   

             Planet  Right Arm Ships  Stars Window special  \
ID                                                           
6598     Large Trio  Handcrank     -      0   Bolt       -   
5470  Asteroid Belt      Swipe     -      0   Bolt       -   
8885           Blue      Pizza     -      1   Blue       -   

                                                   Link Celestialstype  
ID                                                                      
6598  https://opensea.io/assets/0x8184a482a5038b124d...      Starsonly  
5470  https://opensea.io/assets/0x8184a482a5038b124d...   Galaxiesonly  
8885  https://opensea.io/assets/0x8184a482a5038b124d...      Starsonly

Name  Price Psymbol  Lastprice LPsymbol              LPdate  Probscore  \
ID                                                                             
6368  6368  0.650     ETH       0.24      ETH 2021-09-11 01:19:06   6.526534   
1686  1686  0.715     ETH        NaN      NaN                 NaT   0.529944   
5973  5973  0.850     ETH       0.71      ETH 2021-10-08 23:50:24   3.996623   

     Anomaly  Celestial Bodies  Cockpit  Galaxies  Left Arm           Music  \
ID                                                                            
6368       -                 4  Hexagon         1    Thrust     Space Ender   
1686       -                 4    Sound         1     Swipe  Lone Planeteer   
5973       -                 4    Retro         2  Antennae     The Cruiser   

     Panel 1 Panel 2   Panel 3       Panel 4        Panel 5 Planet Right Arm  \
ID                                                                             
6368       -       -         -             -  Radial Static   Moon  Hologram   
1686       -       -      JPEG  Tunnel (alt)           JPEG      -  Antennae   
5973       -       -  Low-poly             -              -      -     Booze   

     Ships  Stars Window special  \
ID                                 
6368     -      3  White       -   
1686     -      3   Pink       -   
5973     -      2  Green       -   

                                                   Link Celestialstype  
ID                                                                      
6368  https://opensea.io/assets/0x8184a482a5038b124d...           Both  
1686  https://opensea.io/assets/0x8184a482a5038b124d...           Both  
5973  https://opensea.io/assets/0x8184a482a5038b124d...           Both

Name   Price Psymbol  Lastprice LPsymbol              LPdate  Probscore  \
ID                                                                              
8624  8624  0.6899     ETH      0.650      ETH 2021-10-09 02:29:19   0.024305   
8198  8198  0.6900     ETH      0.155      ETH 2021-08-15 17:00:44   0.025570   
661    661  0.7700     ETH        NaN      NaN                 NaT   0.238367   

     Anomaly  Celestial Bodies  Cockpit  Galaxies Left Arm         Music  \
ID                                                                         
8624       -                 0  Dotface         0     Porn   Star Ranger   
8198       -                 1  Circles         1     Porn  The Ponderer   
661        -                 2     Dots         0     Bong   Star Ranger   

     Panel 1 Panel 2 Panel 3     Panel 4 Panel 5      Planet  \
ID                                                             
8624       -       -   Waves  Spacecraft       -           -   
8198       -       -   Waves           -  Tunnel  Large Trio   
661        -       -       -           -   Crack   Dark Ring   

              Right Arm             Ships  Stars  Window special  \
ID                                                                 
8624            Shifter         Freighter      0   White       -   
8198  Button Row Slider                 -      0  Purple       -   
661               Swipe  Freighter Battle      2   White       -   

                                                   Link Celestialstype  
ID                                                                      
8624  https://opensea.io/assets/0x8184a482a5038b124d...      Starsonly  
8198  https://opensea.io/assets/0x8184a482a5038b124d...   Galaxiesonly  
661   https://opensea.io/assets/0x8184a482a5038b124d...      Starsonly